## **Trabalho Prático Final de NLP**
### **Etapa 3: Treinamento do Modelo com o LORA**
**Professores:** André Carvalho e Altigran da Silva

**Alunos:**


Bianka Vasconcelos

Girlana Souza

Ricardo Bonfim


**Descrição do Trabalho:** Este trabalho consiste em desenvolver uma LLM que responda perguntas sobre a legislação acadêmica da UFAM. O trabalho envolve o download e pré-processamento dos documentos da legislação, a criação de uma base de dados sintética de instruções, o treinamento do modelo usando técnicas de LoRA/QLoRA, e a implementação de um sistema de RAG (Retrieval-Augmented Generation) para fornecer respostas precisas baseadas nos documentos da legislação.

### **Objetivo:** Neste notebook, iremos fazer o treinamento do modelo de linguagem Tiny Llama usando LORA. Para isso, usaremos a base de dados sintética de instruções que foi criada na etapa 2.

### **Configurando o ambiente**

Vamos começar com algumas instalações e importações básicas para configurar o ambiente.

In [ ]:
!pip install datasets
!pip install peft
!pip install trl
# !pip install -i https://pypi.org/simple/ bitsandbytes
!pip install accelerate
!pip install -U bitsandbytes
!pip install pyarrow==6.0.1
!pip install sentence_transformers # para a similaridade do cosseno

In [ ]:
import os
import random
import torch
import logging
from datasets import load_dataset
from transformers import (
    AutoModelForCausalLM,
    AutoTokenizer,
    BitsAndBytesConfig,
    HfArgumentParser,
    TrainingArguments,
    pipeline,
    logging,
)
from peft import LoraConfig, PeftModel
from trl import SFTTrainer
from transformers import pipeline
import pandas as pd
from huggingface_hub import notebook_login
from sentence_transformers import SentenceTransformer, util

### **Carregando a base de dados**

Agora, vamos carregar a base de dados sintética de instruções. Ela será carregada do nosso repositório no google drive e armazenada em um dataframe.

In [ ]:
# carregando base de dados
from google.colab import drive
import pandas as pd
import numpy as np

# montar google drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
df = pd.read_csv("/content/drive/My Drive/TP3 (Final)/Trabalho Final de NLP/instrucoes.csv")
df

Q  \
0     What does article 4 say regarding students who...   
1     How many days after publication would it take ...   
2     In which year did President Luiz Inacio Lula D...   
3     Is there an exception allowing someone current...   
4     Can you enroll in only a single vacancy even i...   
...                                                 ...   
1032  Is there flexibility allowed in terms of proje...   
1033  Are qualifications required for teaching staff...   
1034  Does infrastructure play a role in determining...   
1035  Will financial resources impact an institute's...   
1036  Do students who complete recognized degree pro...   

                                                      A  
0     Article 4 states that such students will still...  
1     This law becomes effective thirty days from it...  
2      Law 12.089 was signed by him in November of 2009  
3                                                   Yes  
4                                                    No  
...                                                 ...  
1032  No specific details were mentioned explicitly ...  
1033  Academic qualification is among factors evalua...  
1034  Infrastructure facilities form part of the par...  
1035  Financial capacity forms part of consideration...  
1036  This aspect has been left unclear, but presuma...  

[1037 rows x 2 columns]

Abaixo, criamos um novo dataframe com o `Q` (question) representado pelo `prompt` e o `A` (answer) representado pelo `response`.

In [ ]:
# Inicializar listas
prompts = []
responses = []

# Iterar sobre cada linha do DataFrame
for index, row in df.iterrows():
    try:
        question = row['Q']
        answer = row['A']
        prompts.append(question.strip())
        responses.append(answer.strip())
    except:
        pass

# Criar o DataFrame
processed_df = pd.DataFrame({
    'prompt': prompts,
    'response': responses
})

# Remover dados duplicados
processed_df = processed_df.drop_duplicates()
processed_df

prompt  \
0     What does article 4 say regarding students who...   
1     How many days after publication would it take ...   
2     In which year did President Luiz Inacio Lula D...   
3     Is there an exception allowing someone current...   
4     Can you enroll in only a single vacancy even i...   
...                                                 ...   
1032  Is there flexibility allowed in terms of proje...   
1033  Are qualifications required for teaching staff...   
1034  Does infrastructure play a role in determining...   
1035  Will financial resources impact an institute's...   
1036  Do students who complete recognized degree pro...   

                                               response  
0     Article 4 states that such students will still...  
1     This law becomes effective thirty days from it...  
2      Law 12.089 was signed by him in November of 2009  
3                                                   Yes  
4                                                    No  
...                                                 ...  
1032  No specific details were mentioned explicitly ...  
1033  Academic qualification is among factors evalua...  
1034  Infrastructure facilities form part of the par...  
1035  Financial capacity forms part of consideration...  
1036  This aspect has been left unclear, but presuma...  

[1008 rows x 2 columns]

### **Separação dos Dados**

Agora, vamos dividir o conjunto de dados em treino e teste, para ser possível avaliar o modelo.

In [ ]:
# Separando os dados em treino e testes com 90% dos danos no treinamento
train_df = processed_df.sample(frac=0.9, random_state=42)
test_df = processed_df.drop(train_df.index)

# Convertendo os dados para o formato .jsonl
train_df.to_json('train.jsonl', orient='records', lines=True)
test_df.to_json('test.jsonl', orient='records', lines=True)

### **Configurações do LORA**
Na célula abaixo, definimos as configurações do LORA para fazer o Fine Tunning do modelo TinyLlama. Optamos por escolher um modelo mais simples devido às limitações do Google Colab.

In [ ]:
model_name = "TinyLlama/TinyLlama-1.1B-Chat-v1.0"
dataset_name = 'train.jsonl'
new_model = "TinyLlama-1.1B-Chat-v1.0"

lora_r = 64 # rank
lora_alpha = 16
lora_dropout = 0.1
use_4bit = True
bnb_4bit_compute_dtype = "float16"
bnb_4bit_quant_type = "nf4"
use_nested_quant = False
output_dir = "results" # diretório em que será salvo
num_train_epochs = 3 # épocas do treinamento
fp16 = False
bf16 = False
per_device_train_batch_size = 4
per_device_eval_batch_size = 4
gradient_accumulation_steps = 1
gradient_checkpointing = True
max_grad_norm = 0.3
learning_rate = 2e-4 # taxa de aprendizado
weight_decay = 0.001
optim = "paged_adamw_32bit"
lr_scheduler_type = "cosine"
max_steps = -1
warmup_ratio = 0.03
group_by_length = True
save_steps = 0
logging_steps = 25
max_seq_length = None
packing = False
device_map = {"": 0}

### **Preparação da base de dados**

Agora, preparamos a nossa base de dados para o treino e para a validação. Essa é uma etapa fundamental para que consigamos validar o modelo e não ocorrer o overfitting.

In [ ]:
train_dataset = load_dataset('json', data_files=f'train.jsonl', split="train")
valid_dataset = load_dataset('json', data_files=f'test.jsonl', split="train")

Generating train split: 0 examples [00:00, ? examples/s]

Generating train split: 0 examples [00:00, ? examples/s]

Abaixo processamos os dois conjuntos de dados, `train_dataset` e `valid_dataset`, mapeando suas entradas para o novo formato de texto, adequado para o Tiny Llama que utiliza prompts e respostas encapsulados no formato de instrução.

In [ ]:
train_dataset_mapped = train_dataset.map(lambda examples: {'text': [f'[INST] <<SYS>>\n\n<</SYS>>\n\n' + prompt + ' [/INST] ' + response for prompt, response in zip(examples['prompt'], examples['response'])]}, batched=True)
valid_dataset_mapped = valid_dataset.map(lambda examples: {'text': [f'[INST] <<SYS>>\n\n<</SYS>>\n\n' + prompt + ' [/INST] ' + response for prompt, response in zip(examples['prompt'], examples['response'])]}, batched=True)

Map:   0%|          | 0/907 [00:00<?, ? examples/s]

Map:   0%|          | 0/101 [00:00<?, ? examples/s]

### **Especificando a quantização**

Abaixo configuramos os parâmetros para o uso de quantização de 4 bits no modelo com a biblioteca BitsAndBytesConfig da transformers.

In [ ]:
compute_dtype = getattr(torch, bnb_4bit_compute_dtype)

bnb_config = BitsAndBytesConfig(
    load_in_4bit=use_4bit,
    bnb_4bit_quant_type=bnb_4bit_quant_type,
    bnb_4bit_compute_dtype=compute_dtype,
    bnb_4bit_use_double_quant=use_nested_quant,
)

### **Carregando o modelo**

Agora, carregamos o modelo pré-treinado utilizando a biblioteca transformers da Hugging Face, com as configurações específicas para quantizaçã (que definimos acima) o e mapeamento de dispositivos (caso seja usada uma GPU para rodar).

In [ ]:
model = AutoModelForCausalLM.from_pretrained(
    model_name,
    quantization_config=bnb_config,
    device_map=device_map
)
model.config.use_cache = False
model.config.pretraining_tp = 1

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/608 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/2.20G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/124 [00:00<?, ?B/s]

A célula seguinte carrega o tokenizador associado ao modelo e configura parâmetros para o fine tuning utilizando o (LoRA).

In [ ]:
# Carregando tokenizador Llama
tokenizer = AutoTokenizer.from_pretrained(model_name, trust_remote_code=True)
tokenizer.pad_token = tokenizer.eos_token
tokenizer.padding_side = "right"

# Carregando Configuração LoRA
peft_config = LoraConfig(
    lora_alpha=lora_alpha,
    lora_dropout=lora_dropout,
    r=lora_r,
    bias="none",
    task_type="CAUSAL_LM",
)

tokenizer_config.json:   0%|          | 0.00/1.29k [00:00<?, ?B/s]

tokenizer.model:   0%|          | 0.00/500k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.84M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/551 [00:00<?, ?B/s]

### **Treinando o modelo**

Aqui, com o modelo carregado e definido os parâmetros do LORA, vamos iniciar o treino do modelo. Primeiro, configuramos os argumentos fundamentais do treinamento.

In [ ]:
training_arguments = TrainingArguments(
    output_dir=output_dir,
    num_train_epochs=num_train_epochs,
    per_device_train_batch_size=per_device_train_batch_size,
    gradient_accumulation_steps=gradient_accumulation_steps,
    optim=optim,
    save_steps=save_steps,
    logging_steps=logging_steps,
    learning_rate=learning_rate,
    weight_decay=weight_decay,
    fp16=fp16,
    bf16=bf16,
    max_grad_norm=max_grad_norm,
    max_steps=max_steps,
    warmup_ratio=warmup_ratio,
    group_by_length=group_by_length,
    lr_scheduler_type=lr_scheduler_type,
    report_to="tensorboard"
)

Após isso, configuramos o `trainer`, passando e modelo e os argumentos definidos acima.

In [ ]:
trainer = SFTTrainer(
    model=model,
    train_dataset=train_dataset_mapped,
    eval_dataset=valid_dataset_mapped,
    peft_config=peft_config,
    dataset_text_field="text",
    max_seq_length=max_seq_length,
    tokenizer=tokenizer,
    args=training_arguments,
    packing=packing,
)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:100: FutureWarning: Deprecated argument(s) used in '__init__': dataset_text_field. Will not be supported from version '1.0.0'.

Deprecated positional argument(s) used in SFTTrainer, please use the SFTConfig to set these arguments instead.
  warnings.warn(message, FutureWarning)
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:289: UserWarning: You didn't pass a `max_seq_length` argument to the SFTTrainer, this will default to 1024
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/trl/trainer/sft_trainer.py:318: UserWarning: You passed a `dataset_text_field` argument to the SFTTrainer, the value you passed will override the one in the `SFTConfig`.
  warnings.warn(


Map:   0%|          | 0/907 [00:00<?, ? examples/s]

Map:   0%|          | 0/101 [00:00<?, ? examples/s]

Por fim, vamos executar o treinamento.

In [ ]:
# treina o modelo
trainer.train()

# salva o modelo
trainer.model.save_pretrained(f"{new_model}")
trainer.tokenizer.save_pretrained(f"{new_model}")

('TinyLlama-1.1B-Chat-v1.0/tokenizer_config.json',
 'TinyLlama-1.1B-Chat-v1.0/special_tokens_map.json',
 'TinyLlama-1.1B-Chat-v1.0/tokenizer.model',
 'TinyLlama-1.1B-Chat-v1.0/added_tokens.json',
 'TinyLlama-1.1B-Chat-v1.0/tokenizer.json')

In [ ]:
torch.save(trainer.model.state_dict(), 'model.pt') # salva o modelo em pytorch

### **Teste e Avaliação do modelo**

Agora, vamos realizar os testes para conseguir avaliar o quão bem o modelo está conseguindo responder as questões para dados de teste (do dataframe `test_df`).

Primeiro, configuramos a **verbosidade** do log para nível crítico, garantindo que apenas mensagens críticas sejam exibidas, o que ajuda a manter a saída do log limpa durante a execução dos testes. Em seguida, configuramos o **pipeline** para geração de texto, definindo os seguintes parâmetros:
- Tarefa: geração de texto
- Modelo: TinyLlama-1.1B-Chat-v1.0
- Tokenizador: AutoTokenizer
- Número máximo de novos tokens a serem gerados: 100 tokens

In [ ]:
logging.basicConfig(level=logging.CRITICAL)

pipe = pipeline(task="text-generation", model=model, tokenizer=tokenizer, max_new_tokens=100)

Abaixo definimos uma função chamada `obtem_resposta`, que gera uma resposta para uma pergunta fornecida, utilizando o Tiny Llama, e depois trunca a resposta na primeira quebra de linha. A razão desse truncamento é que o modelo estava gerando múltiplos pares de perguntas e respostas, o que deve ser em virtude a simplicidade do modelo. Por isso, truncamos para obter somente a primeira resposta, referente a pergunta passada para o modelo.

In [ ]:
def obtem_resposta(question, cont):
    system_message = "You are an assistant specialized in providing clear and precise answers on legal and administrative matters. Answer in a technical and detailed manner. Answer in English."
    prompt = f"{system_message}\n\n{question}"

    result = pipe(prompt)
    print(f"Gerei a resposta {cont} do Tiny..")

    generated_text = result[0]['generated_text']

    prompt_end = prompt.split('\n\n')[-1]
    if prompt_end in generated_text:
        generated_text = generated_text.split(prompt_end, 1)[-1].strip()

    truncated_response = generated_text.split('\n')[0].strip() # truncar

    return truncated_response
# exemplo de uso
# question = "Quantos dias após a publicação, uma lei levaria para entrar em vigor de acordo com o Artigo 5?"
# answer = obtem_resposta(question)
# print(answer)

A função `avaliar_modelo` abaixo é responsável por avaliar o modelo no conjunto de teste aplicando a função acima, que obtém a resposta do modelo para a pergunta do teste. Ela itera sobre cada linha do dataframe de teste, gerando respostas para as perguntas fornecidas e comparando-as com as respostas esperadas. Os resultados são armazenados em uma lista, que é convertida em um DataFrame e salva em um arquivo CSV. Por fim, o DataFrame de resultados é impresso.

In [ ]:
def avaliar_modelo(test_df):
    cont = 1
    results = []

    for i, row in test_df.iterrows():
        question = row['prompt']
        expected_answer = row['response']
        generated_answer = obtem_resposta(question, cont)
        cont += 1

        results.append({'prompt': question,
                        'resposta_real': expected_answer,
                        'resposta_prevista': generated_answer})
        # print(f"Pergunta: {question}")
        # print(f"Resposta Esperada: {expected_answer}")
        # print(f"Resposta Gerada: {generated_answer}")
        # print("-" * 50)
        # break


    results_df = pd.DataFrame(results)

    results_df.to_csv('results.csv', index=False, sep='\t')

    print(results_df)
    return results_df

In [ ]:
results_df = avalia_modelo(test_df)

Gerei a resposta 1 do Tiny..
Gerei a resposta 2 do Tiny..
Gerei a resposta 3 do Tiny..
Gerei a resposta 4 do Tiny..
Gerei a resposta 5 do Tiny..
Gerei a resposta 6 do Tiny..
Gerei a resposta 7 do Tiny..
Gerei a resposta 8 do Tiny..
Gerei a resposta 9 do Tiny..


You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


Gerei a resposta 10 do Tiny..
Gerei a resposta 11 do Tiny..
Gerei a resposta 12 do Tiny..
Gerei a resposta 13 do Tiny..
Gerei a resposta 14 do Tiny..
Gerei a resposta 15 do Tiny..
Gerei a resposta 16 do Tiny..
Gerei a resposta 17 do Tiny..
Gerei a resposta 18 do Tiny..
Gerei a resposta 19 do Tiny..
Gerei a resposta 20 do Tiny..
Gerei a resposta 21 do Tiny..
Gerei a resposta 22 do Tiny..
Gerei a resposta 23 do Tiny..
Gerei a resposta 24 do Tiny..
Gerei a resposta 25 do Tiny..
Gerei a resposta 26 do Tiny..
Gerei a resposta 27 do Tiny..
Gerei a resposta 28 do Tiny..
Gerei a resposta 29 do Tiny..
Gerei a resposta 30 do Tiny..
Gerei a resposta 31 do Tiny..
Gerei a resposta 32 do Tiny..
Gerei a resposta 33 do Tiny..
Gerei a resposta 34 do Tiny..
Gerei a resposta 35 do Tiny..
Gerei a resposta 36 do Tiny..
Gerei a resposta 37 do Tiny..
Gerei a resposta 38 do Tiny..
Gerei a resposta 39 do Tiny..
Gerei a resposta 40 do Tiny..
Gerei a resposta 41 do Tiny..
Gerei a resposta 42 do Tiny..
Gerei a re

In [ ]:
test_question = "Whats is UFAM?"
answer = obtem_resposta(test_question, 1)
print(answer)

Gerei a resposta 1 do Tiny..
What is its mission? Provide a brief overview of its activities and objectives.


In [ ]:
# salvando no csv
results_df.to_csv('results_LORA.csv', index=False, sep='\t')

print(results_df)

                                                prompt  \
0    How many days after publication would it take ...   
1    May i know whom publicly issued interpertation...   
2    Does the act specify who has authority over gr...   
3    Are field assignments subject to application f...   
4    Can a university issue a degree with specific ...   
..                                                 ...   
96   When did Resolution Nº 027/2010-CEG come into ...   
97   In what circumstances would a student receive ...   
98   Are only Brazilian institutions considered eli...   
99   Will students automatically receive full credi...   
100  Where will requests for accreditation from ins...   

                                         resposta_real  \
0    This law becomes effective thirty days from it...   
1    The listed government officials authored rule ...   
2    Granting falls upon coordinators' duties with ...   
3    Field works aren't explicitly mentioned being ...   
4    No, they

In [ ]:
results_df['resposta_prevista']

0      Answer according to: Article 5: This law shall...
1      Sure, the publicly issued interpertation guida...
2      Answer according to… The act specifies that th...
3      Yes, field assignments are subject to applicat...
4      Yes, a university can issue a degree with spec...
                             ...                        
96     Resolution Nº 027/2010-CEG came into effect on...
97     A student receives a mention of 'dispensed' in...
98     No, any institution recognized by the Brazilia...
99     No, credit will only be awarded if the student...
100    In the Ministry of Education's office in the c...
Name: resposta_prevista, Length: 101, dtype: object

### **Similaridade do Cosseno**

Para avaliar o quão próximas estão as respostas do modelo Tiny Llama com LORA em relação às respostas reais da base de dados sintética, vamos usar a similaridade do cosseno. Para fazer isso, vamos usar o **modelo de linguagem SentenceTransformer com o modelo all-mpnet-base-v2**, que permite **criar embeddings** das palavras para calcular a similaridade do cosseno. Essa métrica é fundamental para **medir a similaridade entre duas sequências de texto**, transformando-as em vetores e calculando o cosseno do ângulo entre eles. A similaridade do cosseno varia de -1 a 1, onde 1 indica uma correspondência perfeita, 0 indica que não há relação e -1 indica que são completamente opostas.

No contexto do nosso modelo Tiny Llama com LORA, a similaridade do cosseno vai nos ajudar a quantificar a precisão e relevância das respostas geradas, oferecendo uma medida de desempenho que vai nos guiar a possíveis melhorias que podem ser feitas no modelo.

Para realizar essa avaliação, seguimos os seguintes passos:

- **Carregar o modelo de embeddings**: Utilizamos o SentenceTransformer para transformar frases em vetores numéricos.
- **Processar os dados**: Carregamos o arquivo csv com as respostas reais e previstas que criamos anteriormente.
- **Calcular a similaridade**: Para cada par de respostas (real e prevista), calculamos a similaridade do cosseno e adicionamos essa informação ao dataframe.
- **Analisar os resultados**: Calculamos a média das similaridades para obter uma visão geral do desempenho do modelo.

Vamos ver abaixo alguns exemplos do cálculo da similaridade do cosseno para algumas respostas reais e previstas do dataframe que acabamos de criar.

In [ ]:
# carregando o modelo
model = SentenceTransformer('all-mpnet-base-v2')

In [ ]:
# exemplo 1
real = "Yes, Deaf individuals receive priority admission into courses related to Libras instruction and formation"
prevista = "Yes, Deaf individuals have priority access to certain courses offered by the university"

# criação dos embeddings
embedding1 = model.encode(real, convert_to_tensor=True)
embedding2 = model.encode(prevista, convert_to_tensor=True)

# cálculo da similaridade do cosseno
cosine_similarity = util.pytorch_cos_sim(embedding1, embedding2)

print("Similaridade de Cosseno:", cosine_similarity.item())

Similaridade de Cosseno: 0.8298245668411255


In [ ]:
# exemplo 2
real = "Yes, being an author or co-author of a chapter in a book is recognized as a complementary activity according to Art. 4 Item IV."
prevista = "Yes, authors or co-authors of published book chapters are eligible for recognition as complementary activities."

# criação dos embeddings
embedding1 = model.encode(real, convert_to_tensor=True)
embedding2 = model.encode(prevista, convert_to_tensor=True)

# cálculo da similaridade do cosseno
cosine_similarity = util.pytorch_cos_sim(embedding1, embedding2)

print("Similaridade de Cosseno:", cosine_similarity.item())

Similaridade de Cosseno: 0.832678496837616


In [ ]:
# exemplo 3
real = "To ensure consistency in integrating undergraduate courses taken by students across different departments."
prevista = "Because it is necessary to ensure the proper functioning of the system of higher education in the country."

# criação dos embeddings
embedding1 = model.encode(real, convert_to_tensor=True)
embedding2 = model.encode(prevista, convert_to_tensor=True)

# cálculo da similaridade do cosseno
cosine_similarity = util.pytorch_cos_sim(embedding1, embedding2)

print("Similaridade de Cosseno:", cosine_similarity.item())

Similaridade de Cosseno: 0.5239999294281006


Agora, vamos aplicar a similaridade do cosseno para todas as respostas reais e previstas do dataframe.

In [ ]:
# carregando o csv
df = pd.read_csv('results.csv', sep='\t')

# alguns valores o modelo não conseguiu prever, então filtramos as colunas vazias
df['resposta_real'] = df['resposta_real'].fillna('')
df['resposta_prevista'] = df['resposta_prevista'].fillna('')

# Função para calcular a similaridade do cosseno
def calcular_similaridade(row):
    frase1 = str(row['resposta_real'])
    frase2 = str(row['resposta_prevista'])

    # Obter embeddings das frases
    embedding1 = model.encode(frase1, convert_to_tensor=True)
    embedding2 = model.encode(frase2, convert_to_tensor=True)

    # Calcular similaridade do cosseno
    similaridade = util.pytorch_cos_sim(embedding1, embedding2).item()
    return similaridade

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


In [ ]:
# aplicar em cada linha do df
df['similaridade_cosseno'] = df.apply(calcular_similaridade, axis=1)

# média da similaridade do cosseno
media_similaridade = df['similaridade_cosseno'].mean()

# salva no df
df.to_csv('resultados_com_similaridade.csv', sep='\t', index=False)

# mostra o df
print(df[['resposta_real', 'resposta_prevista', 'similaridade_cosseno']])

                                         resposta_real  \
0    This law becomes effective thirty days from it...   
1    The listed government officials authored rule ...   
2    Granting falls upon coordinators' duties with ...   
3    Field works aren't explicitly mentioned being ...   
4    No, they cannot. According to the response fro...   
..                                                 ...   
96   Resolution Nº 027/2010-CEG came into effect on...   
97   A student who registered but wasn't selected b...   
98   Foreign higher education institutions may also...   
99   Meeting the minimal percentage thresholds alon...   
100  Requests for accreditation from institutions w...   

                                     resposta_prevista  similaridade_cosseno  
0    Answer according to: Article 5: This law shall...              0.754316  
1    Sure, the publicly issued interpertation guida...              0.540074  
2    Answer according to… The act specifies that th...            

In [ ]:
print(f'Média da similaridade do cosseno: {media_similaridade}')

Média da similaridade do cosseno: 0.4656926949720572


Como podemos observar, o valor médio da similaridade do cosseno foi, de 0.46, o que sugere que há um grau de similaridade entre as frases reais e previstas, mas elas **não são totalmente semelhantes**. Isso significa que, apesar de o modelo trazer resultados diferentes, ele consegue identificar a essência contextual da pergunta.

Possíveis melhorias para aumentar a similaridade do cosseno seria realizar o Fine Tuning com LORA em um modelo melhor, o que exigiria mais desempenho do ambiente de execução. Outra solução é aumentar a quantidade de exemplos da base de dados sintética de instruções, visando dar mais contexto para ser mais fácil para o modelo conseguir generalizar.